In [2]:
# !pip show openai-whisper
%cd ..
!ls

/work/van-speech-nlp/jindaznb/jslpnb/mllm_expriments/Whispering-LLaMA
convert_hf_checkpoint.py	   images	     runs
data_preparation		   Inference	     training
demo.ipynb			   LICENSE	     weights
EMNLP__4032_Whispering_LLaMA_.pdf  lit_llama	     whisper_openAI
environment.yml			   README.md
generate			   requirements.txt


In [2]:
import os
from dataclasses import dataclass, field, replace
from typing import TYPE_CHECKING, Dict, Iterable, List, Optional, Sequence, Tuple, Union
import whisper_openAI.whisper as whisper
import torch
from whisper_openAI.whisper.tokenizer import Tokenizer, get_tokenizer
import torch
import torch.nn.functional as F
from torch import Tensor

# We get the acoustic embeddings from Whisper Large V2
model,processor = whisper.load_model("large-v2")
# model,processor = whisper.load_model("medium")

100%|█████████████████████████████████████| 2.87G/2.87G [02:36<00:00, 19.8MiB/s]


In [3]:
model.eval()

Whisper(
  (encoder): AudioEncoder(
    (conv1): Conv1d(80, 1280, kernel_size=(3,), stride=(1,), padding=(1,))
    (conv2): Conv1d(1280, 1280, kernel_size=(3,), stride=(2,), padding=(1,))
    (blocks): ModuleList(
      (0-31): 32 x ResidualAttentionBlock(
        (attn): MultiHeadAttention(
          (query): Linear(in_features=1280, out_features=1280, bias=True)
          (key): Linear(in_features=1280, out_features=1280, bias=False)
          (value): Linear(in_features=1280, out_features=1280, bias=True)
          (out): Linear(in_features=1280, out_features=1280, bias=True)
        )
        (attn_ln): LayerNorm((1280,), eps=1e-05, elementwise_affine=True)
        (mlp): Sequential(
          (0): Linear(in_features=1280, out_features=5120, bias=True)
          (1): GELU(approximate='none')
          (2): Linear(in_features=5120, out_features=1280, bias=True)
        )
        (mlp_ln): LayerNorm((1280,), eps=1e-05, elementwise_affine=True)
      )
    )
    (ln_post): LayerNorm((

In [4]:
pwd

'/work/van-speech-nlp/jindaznb/jslpnb/mllm_expriments/Whispering-LLaMA'

In [1]:
import json
k=17
# The below is the json file you can generate using the "To generatn-best hyporhesis.ipynb" notebook; Need to further tokenize the hypothesis

with open(f'Inference/gs_inferences/{k}Science and Technology.json', "r") as file: #change
    test_data = json.load(file)

FileNotFoundError: [Errno 2] No such file or directory: 'Inference/gs_inferences/17Science and Technology.json'

In [6]:
test_data

[{'POD0000006044_S0000046': {'temp': 0.79,
   'path': '/work/van-speech-nlp/jindaznb/jslpnb/cache1/downloads/extracted/9fb7dc35259507ddd2d143e7481a89a28429fadd1410efeb94c218730cbd35c2/s_chunks_0000/POD0000006044_S0000046.wav',
   'ground_truth': "it's in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data.",
   'inference': ['and in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
    'and some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
    'as i mentioned before in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
    'but its in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
    'in some ways is very similar to some of the challenges that companies are deali

In [7]:
# !pip install safetensors

In [8]:
"""Implementation derived from https://github.com/tloen/alpaca-lora"""
import sys
from pathlib import Path
import torch
import requests
import json
import os 

from lit_llama.tokenizer import Tokenizer
from tqdm import tqdm

In [9]:
tokenizer_path: Path = Path("weights/tokenizer.model")
tokenizer = Tokenizer(tokenizer_path)
train_set =test_data
print(f"train has {len(train_set):,} samples")
print("Processing train split ...")

train has 11,320 samples
Processing train split ...


In [10]:
model.device

device(type='cuda', index=0)

In [11]:
result = []

def tokenize(tokenizer: Tokenizer, string: str, max_length: int, eos=True) -> torch.Tensor:
    return tokenizer.encode(string, bos=True, eos=eos, max_length=max_length)

instruction = 'You are an ASR transcript selector. You have a few transcripts generated by an automatic speech recognition model. Your task is to generate the most likely transcript from them. If the generated transcripts have grammatical or logical errors, you will modify them accordingly to produce the most accurate and coherent transcript.'

for i in tqdm(range(len(test_data))):        
    for name in test_data[i].keys():
        ip = test_data[i][name]
    inference = ip['inference']
    gt = ip['ground_truth']
        
    # Removing the ground_truth, if present among the inferences for the prompt
    if gt in inference:
        inference.remove(gt)
            
        # joining the inputs with '\n'
    for_input = '\n'.join(inference[:15])
    # The prompt follows the Aplaca template ; https://github.com/tatsu-lab/stanford_alpaca
    full_prompt = f"""Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.\n\n ### Instruction:\n{instruction}\n\n### Input:\n{for_input}\n\n### Response:"""
    full_prompt_and_response = full_prompt + gt

    encoded_full_prompt = tokenize(tokenizer, full_prompt, max_length=2048, eos=False)
    encoded_full_prompt_and_response = tokenize(tokenizer, full_prompt_and_response, eos=True, max_length=2048)
    labels = encoded_full_prompt_and_response.clone()
    labels_with_masked_input = encoded_full_prompt_and_response.clone()
    labels_with_masked_input[:len(encoded_full_prompt)] = -1
    
    path =  ip['path']
    audio = whisper.load_audio(path)  
    audio = whisper.pad_or_trim(audio)            
    mel = whisper.log_mel_spectrogram(audio).to(model.device)  # of shape (#channels =  80 ; #samples = )   
    mel = mel.unsqueeze(0)
    
    with torch.no_grad():
        audio_features  = model.encoder(mel)
        

    result.append( {**ip,'index':name, "input_ids": encoded_full_prompt_and_response, "input_ids_no_response": encoded_full_prompt, "labels": labels, 'labels_with_masked_input': labels_with_masked_input,'audio_features': audio_features.bfloat16()})

100%|██████████| 11320/11320 [33:08<00:00,  5.69it/s]


In [18]:
import pickle

# Define the file path
output_file = f'Inference/gs_inferences/{k}_result.pkl'

# Save the result variable to a file
with open(output_file, 'wb') as f:
    pickle.dump(result, f)

In [ ]:
print(len(result))
result[0]

In [13]:
torch.save(result,'Inference/gs_inferences/gigaspeech_train.pt')

In [1]:
print()

In [4]:
import torch
train_data = torch.load('Inference/gs_inferences/gigaspeech_train.pt',map_location=torch.device('cpu'))

In [5]:
len(train_data)

11320

In [7]:
import random

k=17
total_samples = len(train_data)
test_size = 1000

# Randomly select 1000 samples for the test set
test_indices = random.sample(range(total_samples), test_size)
train_indices = [i for i in range(total_samples) if i not in test_indices]

# Split the dataset into train and test sets
train_set = [train_data[i] for i in train_indices]
test_set = [train_data[i] for i in test_indices]


In [8]:
len(train_set)

10320

In [9]:
len(test_set)

1000

In [10]:

# Save train and test sets into separate .pt files
torch.save(train_set, f'Inference/gs_inferences/{k}_train.pt')
torch.save(test_set, f'Inference/gs_inferences/{k}_test.pt')

In [13]:
train_set[0]

{'temp': 0.79,
 'path': '/work/van-speech-nlp/jindaznb/jslpnb/cache1/downloads/extracted/9fb7dc35259507ddd2d143e7481a89a28429fadd1410efeb94c218730cbd35c2/s_chunks_0000/POD0000006044_S0000046.wav',
 'ground_truth': "it's in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data.",
 'inference': ['and in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
  'and some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
  'as i mentioned before in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
  'but its in some ways very similar to some of the challenges that companies are dealing with today in terms of streaming data',
  'in some ways is very similar to some of the challenges that companies are dealing with today in terms of streaming data',